In [1]:
import emoji
import numpy as np
import pandas as pd
from sklearn.preprocessing import LabelEncoder
from transformers import AutoTokenizer

In [2]:
# train_df=pd.read_csv('/DATA/sin-kaf/offenseval-tr-training-v1.tsv',sep='\t')
# test_df=pd.read_csv('/DATA/sin-kaf/offenseval-tr-testset-v1.tsv',sep='\t')
# augmented_df=pd.read_csv('augmented_data_offensive.csv')
# selin_df=pd.read_csv('/DATA/sin-kaf/selin_data.csv')

In [3]:
outliers_df=pd.read_csv('/DATA/sin-kaf/cluster_outliers.csv')
outliers_df=outliers_df.drop(['Unnamed: 0'], axis=1)
outliers_df['subtask_a'] = outliers_df['subtas_a']
outliers_df=outliers_df.drop(['subtas_a'], axis=1)


In [4]:
train_df=outliers_df

In [5]:
# augmented_df=augmented_df.drop(['Unnamed: 0'], axis=1)
# augmented_df = augmented_df.dropna()
# train_df=pd.concat([train_df,augmented_df], axis=0)
# train_df=pd.concat([train_df,test_df], axis=0)
# train_df=train_df.drop(['id'], axis=1)
data=train_df['tweet'].tolist()
for i in range(len(data)):
    data[i] = data[i].replace('@USER','')
    data[i] = data[i].replace('#','')
    data[i] = data[i].replace('$','')
    data[i] = emoji.demojize(data[i])
    
train_df['tweet'] = data
lab = LabelEncoder()
train_df['subtask_a'] = lab.fit_transform(train_df['subtask_a'])
df = train_df[train_df.subtask_a != 2]

In [6]:
train_df

tweet  subtask_a
0       en güzel uyuyan insan ödülü jeon jungkook'a g...          0
1       Mekanı cennet olsun, saygılar sayın avukatımı...          0
2      Kızlar aranızda kas yığını beylere düşenler ol...          0
3      Biraz ders çalışayım. Tembellik ve uyku düşman...          0
4          Trezeguet yerine El Sharawy daha iyi olmaz mı          0
...                                                  ...        ...
41177  Hil**adamlar kesinlikle kelimeleri anlamıyorla...          1
41178  Böyle piçlerin çok erken ölmemelerini ve çok f...          1
41179  Turgay denilen bu holigonda bir sorun yok, gur...          1
41180  Umarım ülkenin düşük zekadan kurtulması ilgile...          1
41181  CHP sandıkları bırakmaz, üzerine oturur, bir c...          1

[41182 rows x 2 columns]

In [7]:
# train_df=pd.concat([train_df,selin_df], axis=0)

In [8]:
train_df

tweet  subtask_a
0       en güzel uyuyan insan ödülü jeon jungkook'a g...          0
1       Mekanı cennet olsun, saygılar sayın avukatımı...          0
2      Kızlar aranızda kas yığını beylere düşenler ol...          0
3      Biraz ders çalışayım. Tembellik ve uyku düşman...          0
4          Trezeguet yerine El Sharawy daha iyi olmaz mı          0
...                                                  ...        ...
41177  Hil**adamlar kesinlikle kelimeleri anlamıyorla...          1
41178  Böyle piçlerin çok erken ölmemelerini ve çok f...          1
41179  Turgay denilen bu holigonda bir sorun yok, gur...          1
41180  Umarım ülkenin düşük zekadan kurtulması ilgile...          1
41181  CHP sandıkları bırakmaz, üzerine oturur, bir c...          1

[41182 rows x 2 columns]

In [9]:
train_df = df.sample(frac = 0.7, random_state = 200)
df_2 = df.drop(train_df.index)
test_df = df_2.sample(frac = 0.15, random_state = 200)
val_df = df_2.drop(test_df.index)

In [10]:
text_train = train_df.tweet.values
label_train = train_df.subtask_a.values

In [11]:
text_test = test_df.tweet.values
label_test = test_df.subtask_a.values

In [12]:
text_val = val_df.tweet.values
label_val = val_df.subtask_a.values

In [13]:
from datasets.dataset_dict import DatasetDict
from datasets import Dataset
dataset={'train':Dataset.from_dict({'label':label_train,'text':text_train}),
        'val':Dataset.from_dict({'label':label_val,'text':text_val}),
        'test':Dataset.from_dict({'label':label_test,'text':text_test})
        }
dataset = DatasetDict(dataset)

In [14]:
# tokenizer = AutoTokenizer.from_pretrained("dbmdz/bert-base-turkish-128k-uncased")
# tokenizer = AutoTokenizer.from_pretrained("dbmdz/distilbert-base-turkish-cased")
tokenizer = AutoTokenizer.from_pretrained("Overfit-GM/distilbert-base-turkish-cased-offensive")
# tokenizer = AutoTokenizer.from_pretrained("Overfit-GM/distilbert-base-turkish-cased-offensive",max_length=208,padding="max_length",truncation=True,return_tensors="pt",add_special_tokens=True,)
# tokenizer = AutoTokenizer.from_pretrained("stage_f/pretrain_mlm_distilbert-base-turkish-cased")
def tokenize_function(examples):
    return tokenizer(examples["text"], padding="max_length", truncation=True)

In [15]:
tokenized_datasets = dataset.map(tokenize_function, batched=True)

Map:   0%|          | 0/28827 [00:00<?, ? examples/s]

Map:   0%|          | 0/10502 [00:00<?, ? examples/s]

Map:   0%|          | 0/1853 [00:00<?, ? examples/s]

In [16]:
small_train_dataset = tokenized_datasets["train"].shuffle(seed=42)
small_eval_dataset = tokenized_datasets["test"].shuffle(seed=42)

In [17]:
small_train_dataset

Dataset({
    features: ['label', 'text', 'input_ids', 'attention_mask'],
    num_rows: 28827
})

In [18]:
small_eval_dataset

Dataset({
    features: ['label', 'text', 'input_ids', 'attention_mask'],
    num_rows: 1853
})

In [19]:
from transformers import AutoModelForSequenceClassification

# model = AutoModelForSequenceClassification.from_pretrained("dbmdz/bert-base-turkish-128k-uncased",num_labels = 2)
# model = AutoModelForSequenceClassification.from_pretrained("dbmdz/distilbert-base-turkish-cased",num_labels = 2)
# model = AutoModelForSequenceClassification.from_pretrained("Overfit-GM/distilbert-base-turkish-cased-offensive",num_labels = 2, ignore_mismatched_sizes=True)
model = AutoModelForSequenceClassification.from_pretrained("Overfit-GM/distilbert-base-turkish-cased-offensive",num_labels = 2, ignore_mismatched_sizes=True)

Some weights of DistilBertForSequenceClassification were not initialized from the model checkpoint at Overfit-GM/distilbert-base-turkish-cased-offensive and are newly initialized because the shapes did not match:
- classifier.weight: found shape torch.Size([5, 768]) in the checkpoint and torch.Size([2, 768]) in the model instantiated
- classifier.bias: found shape torch.Size([5]) in the checkpoint and torch.Size([2]) in the model instantiated
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [20]:
from transformers import TrainingArguments

training_args = TrainingArguments(output_dir="test_trainer")

In [21]:
# import numpy as np
# import evaluate

# # metric = evaluate.load("accuracy")
# # confusion_matrix = evaluate.load("BucketHeadP65/confusion_matrix")
# # metric = evaluate.combine(["accuracy", "f1", "precision", "recall", "confusion_matrix"])
# metric = evaluate.combine(["accuracy", "f1", "precision", "recall"])

In [22]:
import numpy as np
import evaluate

metric = evaluate.combine(["accuracy", "f1", "precision", "recall"])
conf_matrix = evaluate.load("BucketHeadP65/confusion_matrix")

In [23]:
def compute_metrics(eval_pred):
    logits, labels = eval_pred
    predictions = np.argmax(logits, axis=-1)
    print(conf_matrix.compute(predictions=predictions, references=labels))
    return metric.compute(predictions=predictions, references=labels)

In [24]:
from transformers import TrainingArguments, Trainer
from pytorch_lightning.loggers import TensorBoardLogger,MLFlowLogger

training_args = TrainingArguments(output_dir="test_trainer", evaluation_strategy="epoch", num_train_epochs = 5, logging_dir ='TensorBoard',report_to ='mlflow')

In [25]:
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=small_train_dataset,
    eval_dataset=small_eval_dataset,
    compute_metrics=compute_metrics,
)

In [26]:
trainer.train()

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


  0%|          | 0/18020 [00:00<?, ?it/s]

{'loss': 0.4638, 'learning_rate': 4.86126526082131e-05, 'epoch': 0.14}
{'loss': 0.3886, 'learning_rate': 4.72253052164262e-05, 'epoch': 0.28}
{'loss': 0.3893, 'learning_rate': 4.583795782463929e-05, 'epoch': 0.42}
{'loss': 0.3594, 'learning_rate': 4.445061043285239e-05, 'epoch': 0.55}
{'loss': 0.3547, 'learning_rate': 4.306326304106548e-05, 'epoch': 0.69}
{'loss': 0.3384, 'learning_rate': 4.167591564927858e-05, 'epoch': 0.83}
{'loss': 0.3498, 'learning_rate': 4.028856825749168e-05, 'epoch': 0.97}


  0%|          | 0/232 [00:00<?, ?it/s]

{'confusion_matrix': array([[966,  90],
       [118, 679]])}
{'eval_loss': 0.28741681575775146, 'eval_accuracy': 0.8877495952509444, 'eval_f1': 0.8671775223499362, 'eval_precision': 0.88296488946684, 'eval_recall': 0.8519447929736512, 'eval_runtime': 11.4928, 'eval_samples_per_second': 161.231, 'eval_steps_per_second': 20.186, 'epoch': 1.0}
{'loss': 0.2449, 'learning_rate': 3.890122086570477e-05, 'epoch': 1.11}
{'loss': 0.2178, 'learning_rate': 3.751387347391787e-05, 'epoch': 1.25}
{'loss': 0.2431, 'learning_rate': 3.612652608213097e-05, 'epoch': 1.39}
{'loss': 0.2261, 'learning_rate': 3.4739178690344064e-05, 'epoch': 1.53}
{'loss': 0.2365, 'learning_rate': 3.3351831298557165e-05, 'epoch': 1.66}
{'loss': 0.2169, 'learning_rate': 3.196448390677026e-05, 'epoch': 1.8}
{'loss': 0.222, 'learning_rate': 3.0577136514983354e-05, 'epoch': 1.94}


...

  0%|          | 0/232 [00:00<?, ?it/s]

{'confusion_matrix': array([[966,  90],
       [109, 688]])}
{'eval_loss': 0.824292778968811, 'eval_accuracy': 0.8926065839179709, 'eval_f1': 0.8736507936507937, 'eval_precision': 0.884318766066838, 'eval_recall': 0.863237139272271, 'eval_runtime': 11.6185, 'eval_samples_per_second': 159.487, 'eval_steps_per_second': 19.968, 'epoch': 4.0}
{'loss': 0.0354, 'learning_rate': 9.766925638179801e-06, 'epoch': 4.02}
{'loss': 0.0165, 'learning_rate': 8.379578246392897e-06, 'epoch': 4.16}
{'loss': 0.0119, 'learning_rate': 6.992230854605994e-06, 'epoch': 4.3}
{'loss': 0.0145, 'learning_rate': 5.60488346281909e-06, 'epoch': 4.44}
{'loss': 0.0169, 'learning_rate': 4.217536071032187e-06, 'epoch': 4.58}
{'loss': 0.0132, 'learning_rate': 2.830188679245283e-06, 'epoch': 4.72}
{'loss': 0.0232, 'learning_rate': 1.4428412874583796e-06, 'epoch': 4.86}
{'loss': 0.0189, 'learning_rate': 5.549389567147614e-08, 'epoch': 4.99}


  0%|          | 0/232 [00:00<?, ?it/s]

{'confusion_matrix': array([[955, 101],
       [111, 686]])}
{'eval_loss': 0.937654972076416, 'eval_accuracy': 0.8855909336211549, 'eval_f1': 0.8661616161616161, 'eval_precision': 0.8716645489199492, 'eval_recall': 0.8607277289836889, 'eval_runtime': 11.5644, 'eval_samples_per_second': 160.233, 'eval_steps_per_second': 20.062, 'epoch': 5.0}
{'train_runtime': 3027.4521, 'train_samples_per_second': 47.609, 'train_steps_per_second': 5.952, 'train_loss': 0.15528733040680712, 'epoch': 5.0}


TrainOutput(global_step=18020, training_loss=0.15528733040680712, metrics={'train_runtime': 3027.4521, 'train_samples_per_second': 47.609, 'train_steps_per_second': 5.952, 'train_loss': 0.15528733040680712, 'epoch': 5.0})

# best case

In [25]:
trainer.train()

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


  0%|          | 0/18825 [00:00<?, ?it/s]

{'loss': 0.4623, 'learning_rate': 4.867197875166003e-05, 'epoch': 0.13}
{'loss': 0.3955, 'learning_rate': 4.734395750332006e-05, 'epoch': 0.27}
{'loss': 0.3695, 'learning_rate': 4.601593625498008e-05, 'epoch': 0.4}
{'loss': 0.368, 'learning_rate': 4.4687915006640105e-05, 'epoch': 0.53}
{'loss': 0.3418, 'learning_rate': 4.335989375830013e-05, 'epoch': 0.66}
{'loss': 0.3519, 'learning_rate': 4.203187250996016e-05, 'epoch': 0.8}
{'loss': 0.3418, 'learning_rate': 4.070385126162019e-05, 'epoch': 0.93}


  0%|          | 0/242 [00:00<?, ?it/s]

{'eval_loss': 0.2548353374004364, 'eval_accuracy': 0.9013429752066116, 'eval_f1': 0.8737607402511566, 'eval_precision': 0.9218967921896792, 'eval_recall': 0.8304020100502513, 'eval_runtime': 12.1488, 'eval_samples_per_second': 159.357, 'eval_steps_per_second': 19.92, 'epoch': 1.0}
{'loss': 0.2884, 'learning_rate': 3.9375830013280215e-05, 'epoch': 1.06}
{'loss': 0.2136, 'learning_rate': 3.804780876494024e-05, 'epoch': 1.2}
{'loss': 0.2422, 'learning_rate': 3.671978751660027e-05, 'epoch': 1.33}
{'loss': 0.2105, 'learning_rate': 3.53917662682603e-05, 'epoch': 1.46}
{'loss': 0.2203, 'learning_rate': 3.406374501992032e-05, 'epoch': 1.59}
{'loss': 0.2455, 'learning_rate': 3.2735723771580345e-05, 'epoch': 1.73}
{'loss': 0.2282, 'learning_rate': 3.140770252324037e-05, 'epoch': 1.86}
{'loss': 0.2328, 'learning_rate': 3.00796812749004e-05, 'epoch': 1.99}


...

  0%|          | 0/242 [00:00<?, ?it/s]

{'eval_loss': 0.6084339618682861, 'eval_accuracy': 0.9121900826446281, 'eval_f1': 0.8933500627352573, 'eval_precision': 0.8922305764411027, 'eval_recall': 0.8944723618090452, 'eval_runtime': 11.9875, 'eval_samples_per_second': 161.502, 'eval_steps_per_second': 20.188, 'epoch': 4.0}
{'loss': 0.0175, 'learning_rate': 8.831341301460823e-06, 'epoch': 4.12}
{'loss': 0.0248, 'learning_rate': 7.503320053120851e-06, 'epoch': 4.25}
{'loss': 0.0212, 'learning_rate': 6.175298804780877e-06, 'epoch': 4.38}
{'loss': 0.0215, 'learning_rate': 4.847277556440903e-06, 'epoch': 4.52}
{'loss': 0.0216, 'learning_rate': 3.51925630810093e-06, 'epoch': 4.65}
{'loss': 0.0169, 'learning_rate': 2.1912350597609563e-06, 'epoch': 4.78}
{'loss': 0.0199, 'learning_rate': 8.632138114209828e-07, 'epoch': 4.91}


  0%|          | 0/242 [00:00<?, ?it/s]

{'eval_loss': 0.6909418106079102, 'eval_accuracy': 0.9158057851239669, 'eval_f1': 0.8963763509218055, 'eval_precision': 0.9073359073359073, 'eval_recall': 0.885678391959799, 'eval_runtime': 12.1798, 'eval_samples_per_second': 158.952, 'eval_steps_per_second': 19.869, 'epoch': 5.0}
{'train_runtime': 3197.4084, 'train_samples_per_second': 47.101, 'train_steps_per_second': 5.888, 'train_loss': 0.15457879885892628, 'epoch': 5.0}


TrainOutput(global_step=18825, training_loss=0.15457879885892628, metrics={'train_runtime': 3197.4084, 'train_samples_per_second': 47.101, 'train_steps_per_second': 5.888, 'train_loss': 0.15457879885892628, 'epoch': 5.0})

# load model

In [20]:
import torch

In [21]:
model = AutoModelForSequenceClassification.from_pretrained('/DATA/sin-kaf/test_trainer/checkpoint-16000')

In [30]:
sent = 'güzel kızz'
input_ids = []
attention_masks = []

encoded_dict = tokenizer.encode_plus(
                    sent,
                    add_special_tokens = True,
                    max_length = 64,
                    pad_to_max_length = True,
                    return_attention_mask = True,
                    return_tensors = 'pt',
                )


input_ids = encoded_dict['input_ids']
attention_masks = encoded_dict['attention_mask']


input_ids = torch.cat([input_ids], dim=0)
input_mask = torch.cat([attention_masks], dim=0)



print('Original: ', sent)
print('Token IDs:', input_ids)
print('Token IDs:', input_mask)

Original:  güzel kızz
Token IDs: tensor([[   2, 2639, 2889, 1050,    3,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0]])
Token IDs: tensor([[1, 1, 1, 1, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0,
         0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])


In [31]:
outputs = model(input_ids, input_mask)

In [32]:
outputs

SequenceClassifierOutput(loss=None, logits=tensor([[ 3.6835, -3.6147]], grad_fn=<AddmmBackward0>), hidden_states=None, attentions=None)

In [33]:
torch.argmax(outputs['logits'])

tensor(0)